In [1]:
import pickle
import numpy as np
import torch
import beer

from bokeh.plotting import output_notebook, figure, show, gridplot
from bokeh.models import ColumnDataSource, Range1d, LabelSet, Label
from bokeh.palettes import Category10 as palette

output_notebook()

import plotting

Loading BokehJS ...

In [5]:
with open('exp/globalphone/GE/subspace_monophone_mbn_babel_ldim35/final.mdl', 'rb') as f:
    ploop = pickle.load(f)
    
with open('exp/globalphone/GE/subspace_monophone_mbn_babel_ldim35/gsm_30.mdl', 'rb') as f:
    gsm = pickle.load(f)
    
with open('exp/globalphone/GE/subspace_monophone_mbn_babel_ldim35/units_posts_30.pkl', 'rb') as f:
    lposts, nunits, nstates, groupidx = pickle.load(f)

In [10]:
shmms, lposts = gsm.new_models(100)
shmms[0]

MixtureSet(
  (weights): SubspaceBayesianParameterView(prior=Normal, posterior=NormalDiagonalCovariance)
  (modelset): NormalSet(
    (means_precisions): SubspaceBayesianParameterView(prior=Normal, posterior=NormalDiagonalCovariance)
  )
)

In [12]:
with open('/dev/null', 'wb') as f:
    pickle.dump(3, f)

In [36]:
nunits, nstates, groupidx, len(lposts)

(46, 3, 1, 46)

In [37]:
lposts = model.new_latent_posteriors(10)

AttributeError: 'GSM' object has no attribute 'transform'

In [56]:
models = {
    'latent_dim=2': 'exp/timit/subspace_monophone_mbn_babel_ldim2/pretraining/log/gsm-pretraining.out',
    'gmm_latent_dim=2': 'exp/timit/dsubspace_monophone_mbn_babel_ldim2/pretraining/log/gsm-pretraining.out',
    'latent_dim=5': 'exp/timit/subspace_monophone_mbn_babel_ldim5/pretraining/log/gsm-pretraining.out',
    'gmm_latent_dim=5': 'exp/timit/dsubspace_monophone_mbn_babel_ldim5/pretraining/log/gsm-pretraining.out',
    #'latent_dim=10': 'exp/timit/subspace_monophone_mbn_babel_ldim10/pretraining/log/gsm-pretraining.out',
    #'latent_dim=15': 'exp/timit/subspace_monophone_mbn_babel_ldim15/pretraining/log/gsm-pretraining.out',
    #'latent_dim=20': 'exp/timit/subspace_monophone_mbn_babel_ldim20/pretraining/log/gsm-pretraining.out',
    #'latent_dim=25': 'exp/timit/subspace_monophone_mbn_babel_ldim25/pretraining/log/gsm-pretraining.out',
    #'latent_dim=30': 'exp/timit/subspace_monophone_mbn_babel_ldim30/pretraining/log/gsm-pretraining.out',
    #'latent_dim=40': 'exp/timit/subspace_monophone_mbn_babel_ldim40/pretraining/log/gsm-pretraining.out',
}


def extract_elbos(logfile):
    epochs, elbos = [], []
    with open(logfile, 'r') as f:
        for line in f:
            if 'epoch' in line and 'elbo' in line:
                try:
                    tokens = line.strip().split()[1:]
                    epochs.append(int(tokens[0].split('=')[1]))
                    elbos.append(float(tokens[1].split('=')[1]))
                except:
                    pass
    return epochs, elbos
            
fig = figure()
colors = ['blue', 'red', 'orange', 'green', 'purple', 'brown', 'salmon', 'black']
for item, color in zip(models.items(), colors):
    model, logfile = item
    epochs, elbos = extract_elbos(logfile)
    fig.line(epochs, elbos, legend=model, color=color)
fig.legend.location = 'bottom_right'
show(fig)

In [3]:
figs = []
y_range = x_range = None
dim1 = 0
dim2 = 1
for epoch in range(0, 1, 5):
    with open(f'exp/timit/dsubspace_monophone_mbn_babel_ldim2/{epoch}.mdl', 'rb') as f:
        sploop = pickle.load(f)

    with open(f'exp/timit/dsubspace_monophone_mbn_babel_ldim2/gsm_{epoch}.mdl', 'rb') as f:
        gsm = pickle.load(f)

    with open(f'exp/timit/dsubspace_monophone_mbn_babel_ldim2/units_posts_{epoch}.pkl', 'rb') as f:
        lp_data = pickle.load(f)
        if len(lp_data) == 4:
            latent_posts, nunits, nstates, groupidx = lp_data
            labels = None
        else:
            print('labels')
            latent_posts, nunits, nstates, groupidx, labels = lp_data

    phones = [phone_name for phone_name in sploop.start_pdf]
    phones = phones[2:]
    fig = figure(title=f'Epoch {epoch}')
    
    if x_range is None:
        x_range = fig.x_range
        y_range = fig.y_range
    else:
        fig.x_range = x_range
        fig.y_range = y_range
    if labels is None:
        mean = gsm.latent_prior.mean.numpy()
        cov = gsm.latent_prior.cov.numpy()
        plotting.plot_normal(fig, mean, cov, alpha=.5, color='pink')
    else:
        colors = ['blue', 'orange', 'green', 'red', 'purple', 'brown', 'salmon']
        plotting.plot_gmm(fig, gsm.latent_prior, alpha=.5, colors=colors)
    for phone, latent_post in zip(phones, latent_posts):
        mean = latent_post.params.mean.detach().numpy()
        cov = latent_post.params.diag_cov.detach().diag().numpy()
        plotting.plot_normal(fig, mean, cov, alpha=.3, n_std_dev=1)
        label = Label(x=mean[0], y=mean[1],
                     text=phone, level='glyph')
        fig.add_layout(label)
    figs.append(fig)
    
show(gridplot([figs]))

labels


AttributeError: 'Mixture' object has no attribute 'latent_prior'

In [51]:
figs = []
y_range = x_range = None
y_range2 = x_range2 = None
dim1 = 0
dim2 = 1
classes = sorted(['vowel', 'semi vowel', 'strong fricative', 'weak fricative', 'closure', 'stop', 'nasal'])

for epoch in range(0, 17, 2):
    with open(f'exp/timit/dsubspace_monophone_mbn_babel_ldim2/{epoch}.mdl', 'rb') as f:
        sploop = pickle.load(f)

    with open(f'exp/timit/dsubspace_monophone_mbn_babel_ldim2/gsm_{epoch}.mdl', 'rb') as f:
        gsm = pickle.load(f)

    with open(f'exp/timit/dsubspace_monophone_mbn_babel_ldim2/units_posts_{epoch}.pkl', 'rb') as f:
        lp_data = pickle.load(f)
        latent_posts, nunits, nstates, groupidx, labels = lp_data

    phones = [phone_name for phone_name in sploop.start_pdf]
    phones = phones[2:]
    fig = figure(title=f'within class space (epoch {epoch})')
    
    if x_range is None:
        x_range = fig.x_range
        y_range = fig.y_range
    else:
        fig.x_range = x_range
        fig.y_range = y_range
    mean = gsm.modelset.latent_prior.mean.numpy()
    cov = gsm.modelset.latent_prior.cov.numpy()
    plotting.plot_normal(fig, mean, cov, alpha=.5, color='pink')
    for phone, latent_post in zip(phones, latent_posts):
        mean = latent_post.params.mean.detach().numpy()
        cov = latent_post.params.diag_cov.detach().diag().numpy()
        plotting.plot_normal(fig, mean, cov, alpha=.3, n_std_dev=2)
        label = Label(x=mean[0], y=mean[1],
                     text=phone, level='glyph')
        fig.add_layout(label)
        
    fig2 = figure(title=f'across class space (epoch {epoch})')
    if x_range2 is None:
        x_range2 = fig2.x_range
        y_range2 = fig2.y_range
    else:
        fig2.x_range = x_range2
        fig2.y_range = y_range2
    mean = gsm.modelset.means.prior.mean.numpy()
    cov = gsm.modelset.means.prior.cov.numpy()
    plotting.plot_normal(fig2, mean, cov, alpha=.5, color='pink')
    for i, classname in zip(range(len(gsm.modelset.means.posterior)), classes):
        pdf = gsm.modelset.means.posterior[i]
        mean = pdf.params.mean.detach().numpy()
        cov = pdf.params.diag_cov.detach().diag().numpy()
        plotting.plot_normal(fig2, mean, cov, alpha=.3, n_std_dev=2)
        label = Label(x=mean[0], y=mean[1],
                         text=classname, level='glyph')
        fig2.add_layout(label)
        
    figs.append((fig, fig2))
    
show(gridplot(figs))

In [39]:
classes = sorted(['vowel', 'semi vowel', 'strong fricative', 'weak fricative', 'closure', 'stop', 'nasal'])
classes

['closure',
 'nasal',
 'semi vowel',
 'stop',
 'strong fricative',
 'vowel',
 'weak fricative']

In [40]:
len(gsm.modelset.means.posterior)

7

In [41]:
fig = figure(title=f'Epoch {epoch}')
mean = gsm.modelset.means.prior.mean.numpy()
cov = gsm.modelset.means.prior.cov.numpy()
plotting.plot_normal(fig, mean, cov, alpha=.5, color='pink')
for i, classname in zip(range(len(gsm.modelset.means.posterior)), classes):
    pdf = gsm.modelset.means.posterior[i]
    mean = pdf.params.mean.detach().numpy()
    cov = pdf.params.diag_cov.detach().diag().numpy()
    plotting.plot_normal(fig, mean, cov, alpha=.3, n_std_dev=2)
    label = Label(x=mean[0], y=mean[1],
                     text=classname, level='glyph')
    fig.add_layout(label)
show(fig)

In [79]:
gsm = torch.load(f'exp/timit/subspace_monophone_mbn_babel_gmm_ldim2/gsm_{epoch}.mdl', map_location='cpu')

RuntimeError: Attempting to deserialize object on a CUDA device but torch.cuda.is_available() is False. If you are running on a CPU-only machine, please use torch.load with map_location='cpu' to map your storages to the CPU.

In [76]:
with open(f'exp/timit/subspace_monophone_mbn_babel_gmm_ldim2/gsm_{epoch}.mdl', 'rb') as f:
        gsm = pickle.load(f)

RuntimeError: Attempting to deserialize object on a CUDA device but torch.cuda.is_available() is False. If you are running on a CPU-only machine, please use torch.load with map_location='cpu' to map your storages to the CPU.

In [206]:
figs = []
y_range = x_range = None
dim1 = 3
dim2 = 5
epoch = 0
with open(f'exp/timit/subspace_monophone_mbn_babel_ldim15/{epoch}.mdl', 'rb') as f:
    sploop = pickle.load(f)

with open(f'exp/timit/subspace_monophone_mbn_babel_ldim15/gsm_{epoch}.mdl', 'rb') as f:
    gsm = pickle.load(f)

with open(f'exp/timit/subspace_monophone_mbn_babel_ldim15/units_posts_{epoch}.pkl', 'rb') as f:
    latent_posts, nunits, nstates, groupidx = pickle.load(f)

phones = [phone_name for phone_name in sploop.start_pdf]
phones = phones[2:]
fig = figure(title=f'Epoch {epoch}', width=1500)

if x_range is None:
    x_range = fig.x_range
    y_range = fig.y_range
else:
    fig.x_range = x_range
    fig.y_range = y_range
mean, cov = gsm.latent_prior.mean.numpy(), gsm.latent_prior.cov.numpy()
for dim in range(len(mean)):
    for i, phone, latent_post in zip(range(len(phones)), phones, latent_posts):
        mean = latent_post.params.mean.detach().numpy()
        mean = mean[dim]
        fig.circle(mean, dim)
        label = Label(x=mean, y=dim, text=phone, level='glyph')
        fig.add_layout(label)

show(fig)

In [302]:
with open(f'exp/timit/subspace_monophone_mbn_babel_ldim5/init.mdl', 'rb') as f:
    sploop = pickle.load(f)
sploop.modelset.original_modelset.modelsets[1][9].modelset.means_precisions.stats

tensor([[ -255.2918,   875.9660,  -276.9554,  ...,  -656.3710, -1296.6876,
          1296.6876],
        [ -255.2918,   875.9660,  -276.9554,  ...,  -656.3710, -1296.6876,
          1296.6876],
        [ -255.2918,   875.9660,  -276.9554,  ...,  -656.3710, -1296.6876,
          1296.6876],
        ...,
        [ -255.2918,   875.9660,  -276.9554,  ...,  -656.3710, -1296.6876,
          1296.6876],
        [ -255.2918,   875.9660,  -276.9554,  ...,  -656.3710, -1296.6876,
          1296.6876],
        [ -255.2918,   875.9660,  -276.9554,  ...,  -656.3710, -1296.6876,
          1296.6876]])

In [2]:
with open(f'exp/timit/subspace_monophone_mbn_babel_ldim5/gsm_15.mdl', 'rb') as f:
    gsm = pickle.load(f)

In [10]:
post = gsm.affine_transform.weights.posterior
prior = gsm.affine_transform.weights.prior
beer.dists.kl_div(post, prior)

tensor(82688., grad_fn=<SubBackward0>)